In [ ]:
def Clogit_grad(b,Xbig,ybig,k,J,N,mu0,V0):
    
    b.shape=(len(b),1) #else trouble for prior chunk, will turn 2 x 2, since b comes in as a (2,)
    
    int1=exp(Xbig @ b) #N*J by 1 - each row = xij'beta
    int2=(int1.reshape(N,J)).T #J by N - note reshape collects over rows first, so we first reshaped "the wrong way", then transposed
    #sum for each triplet
    denom = sum(int2,axis=0) #N by 1
    denom.shape=(1,N) #turn into a row vector
    
    #replicate each element in denom j times
    int3=repeat(denom,J) #looks good
    int3.shape=(N*J,1)

    giantP=int1/int3  #OK, shape is 3000 x 1, max<1
    #int4=tile(giantP,k) #3000 x 2, OK
    int4=(tile(giantP,k))*Xbig #3000 x 2, OK

    #now reshape this as follows:
    # convert forst column into a J by N, then add second column (in column dimension), also as a J by N
    int5=(int4.T.reshape(N*k,J)).T  #3 by 2000 as required, visual inspection: looks right

    # obtain sum over columns
    int6 = sum(int5,axis=0)
    int6.shape=(1,N*k)#1 by N*k

    #now reshape this as follows:
    # collect the first N elements into a single column, then add the next N elements as the next column, and so on to get an N by k
    int7=(int6.reshape(k,N)).T  #looks good! N by k

    #pick rows of Xbig for which ybig==1
    #recall Xbig = N*J by k, ybig = N*J by 1
    f1=(ybig==1)
    f1=f1.reshape(Xbig.shape[0])

    pick=Xbig[f1,:] #N by 2, looks good
    int8=sum((pick-int7),axis=0)
    int8.shape=(k,1) #k by 1
    
    priorchunk=(-inv(V0) @ (b-mu0)) #k by 1
    #priorchunk.shape=() #else dimension error in min-function
    #print("shape priorchunk",shape(priorchunk))
        
    G_sum = -(priorchunk+int8) #again, need to invert sign due to minimization
    G_sum.shape=(k,)
    
    return(G_sum)
    
    
    